In [ ]:
import numpy as np
import pandas as pd
import sys


class GSEA:
    def __init(self):
        self.df=None
        self.samp=None
        self.expr_gene=None
        self.pathway_gene_dict = None
        self.largest=None
        self.nt=None
        
    def load_expression_data(self,file_name,drop):
        '''
        input: gene expression filename
        output: pandas dataframe
        '''
        df = pd.read_csv(file_name,sep='\t')
        if drop:
            df = df.drop(columns='SYMBOL')
        #print(df.head())
        return df

    def get_expression_genes(self,df):
        '''
        input: dataframe
        output: list of genes, 10712
        '''
        df_small = df.iloc[:,df.columns=="SYMBOL"]
        #print(df_small.shape)
        print("expression genes:",df_small.head())
        gene_list = df_small.to_numpy().flatten()
        print("len expression genes:",len(gene_list),gene_list.shape)
        return gene_list 

    def load_samples(self,file_name):
        '''
        input: filename of samples
        output: distionary, key=patient name, value=0 healthy, 1 diseased
        '''
        d = {}
        with open(file_name, "r") as fh:
            lines = fh.readlines()
            for line in lines:
                tokens = line.split()
                d[tokens[0]] = tokens[1]
        # print("load_samples d:",d)
        return d
    
    def load_kegg(self,filename):
        '''
        input:kegg file name
        output: dictionary key=KEGG_CITRATE_CYCLE_TCA_CYCLE value=list of genes which are in expression data
        all_genes all genes in all pathways no screening
        hum_genes, only count ones in expression file
        glist only count ones in expression file. glist/path_gene and hum_genes difference? pathgene dict of pathway, list of genes in expressoin
        '''
        path_gene = {}
        with open(filename, "r") as fh:
            lines = fh.readlines()
            #print("len(lines):",len(lines))
            for i in range(0,len(lines)):
                tokens = lines[i].split()
                #print("pathway:",tokens[0])
                genes = tokens[2:]
                #if i==0:
                    #print("lines[i]:",lines[i])
                    #print("tokens[2:]",tokens[2:],len(tokens[2:]))
                #print("pathway genes:",genes,"num pathway genes:",len(genes))
                g_list=[]
                for g in genes:
                    #print("+++++++++++testing g:",g)
                    if g in self.expr_gene:
                        #print("g is in self.expr_gene!!!!!")
                        g_list.append(g)
                        #if gene in expression data add to hum_gene dict
                #if i==0:
                    #print("len g_list, should match later query:",len(g_list))
                path_gene[tokens[0]] = g_list
                #path_gene[tokens[0]] =tokens[2:]
                #print("pathway:",tokens[0]," num genes:",len(g_list))
            #print(" len path_gene:",len(path_gene))
            return path_gene

    
    def load_data(self,expfile,sampfile,keggfile):
        self.samp = self.load_samples(sampfile)
        self.df = self.load_expression_data(expfile,False)       
        self.expr_gene = self.get_expression_genes(self.df)
        print("len expr_gene should be 10k:",len(self.expr_gene))
        #print("expr_gene:",self.expr_gene)
        self.pathway_gene_dict = self.load_kegg(keggfile)
        #print("************")
        #print(self.pathway_gene_dict["KEGG_CITRATE_CYCLE_TCA_CYCLE"])
        #print(len(self.pathway_gene_dict["KEGG_CITRATE_CYCLE_TCA_CYCLE"]))
        #print("************")
        #pathway_gene_dict = load_kegg("c2.cp.kegg.v6.2.symbols.filtered.gmt",expr_gene)
        

    def get_gene_rank_order(self):
        print("------df head--------")
        print(self.df.head())
        print("---------------------")
        rows,cols = self.df.shape
        #build healthy and diseased indexes
        print(self.df.columns)
        healthy_idx=[]
        disease_idx=[]
        for idx,col in enumerate(self.df.columns):
            if col!="SYMBOL":
                print("idx:",idx,"col:",col,self.samp[col])
                if self.samp[col]=='1':
                    disease_idx.append(idx)
                elif self.samp[col]=='0':
                    healthy_idx.append(idx)
                else:
                    print("xxxx")

        print("healthy_idx:",healthy_idx," disease_idx:",disease_idx)
        df_np = self.df.to_numpy()
        print("rows:",rows,"cols:",cols)#fetch healthy as list of columns, diseased as list of columns
        rank_me=[]
        healthy_mean=np.mean(df_np[0,[healthy_idx]])
        disease_mean=np.mean(df_np[0,[disease_idx]])
        print("df_np first 5 rows:",df_np[0:5])
        print("gene rows are by patient, not by healthy and diseased")
        print("before loop healthy_mean:",df_np[0,[healthy_idx]],healthy_mean)
        print("before loop disease_mean:",df_np[0,[disease_idx]],disease_mean)
        print("before loop df_np[0,[healthy_idx]]):",df_np[0,[healthy_idx]])
        print("before loop df_np[0,[disease_idx]]):",df_np[0,[disease_idx]])
        print("df_np.shape[0]:",df_np.shape[0])
        print("before loop diff:",disease_mean-healthy_mean)
        for idx in range(0,df_np.shape[0]):
            healthy_mean=np.mean(df_np[idx,[healthy_idx]])
            disease_mean=np.mean(df_np[idx,[disease_idx]])
            #print("idx:",idx,"healthy_mean:",df_np[0,[healthy_idx]],healthy_mean)
            #print("idx:",idx,"disease_mean:",df_np[0,[disease_idx]],disease_mean)
            #print("idx,diff:",idx,disease_mean-healthy_mean)
            rank_me.append((idx,self.df.iloc[idx,0],disease_mean-healthy_mean)) #sort by second tuple value

        print("length ranked genes: ",len(rank_me))
        #before sorting
        print("rank_me[0:5]",rank_me[0:5])
        largest_test = sorted(rank_me[0:5], key = lambda x: x[2],reverse=True)
        print("largest_test:",largest_test)
        largest_first = sorted(rank_me, key = lambda x: x[2],reverse=True)
        print("largest_first[0:5]",largest_first[0:5],len(largest_first))
        #return list of genes only largest first
        return_me=[]
        for x in largest_first:
            return_me.append(x[1])
        print("return_me[0:5]:",return_me[0:5],len(return_me))
        self.nt=len(return_me)
        self.largest = return_me
        #print("return me:",return_me)
        return return_me
    
    def get_enrichment_score(self,geneset):
        #print("num pathways, should be 145:",len(self.pathway_gene_dict))
        #print("pathway genes",self.pathway_gene_dict[geneset],len(self.pathway_gene_dict[geneset]))
        
        ng = len(self.pathway_gene_dict[geneset])
        nt=self.nt
        penalty_add =np.sqrt((nt-ng)/ng)
        penalty_miss = np.sqrt(ng/(nt-ng))
        #print("ng:",ng," penalty_add:",penalty_add," penalty_miss:",penalty_miss)    
        #calculate ES for each geneset pathway_gene_dict[x] using ranked list. wow for all 10k? 
        es=[]
        es.append(0.)
        sum_es=0.
        for idx in range(0,len(self.largest)):
            print(idx,"processing gene:",self.largest[idx])
            #this is right list? not largest first??? wait the geneset has to be in expressoin data
            if self.largest[idx] in self.pathway_gene_dict[geneset]:
                print("found adding")
                sum_es +=penalty_add
            else:
                print("miss subtracting")
                sum_es-=penalty_miss
            es.append(sum_es)
        #print("es:",es)
        #print("es max:",max(es),round(max(es),2))
        return round(max(es),2)
    
    def q10(self):
        """
        which geneset has highest ES? KEGG_NEUROACTIVE_LIGAND_RECEPTOR_INTERACTION
        """
        score=[]
        for x in self.pathway_gene_dict.keys():
            s = self.get_enrichment_score(x)
            score.append(s)
            print("processing:",x," ES:",s)
        print("q10 max:",max(score))
        
    def q12(self):
        """
        how many unique genes in kegg file
        """
        g=[]
        for x in self.pathway_gene_dict.keys():
            genes = self.pathway_gene_dict[x]
            #print("pathway:",x," genes:",genes)
            g.extend(genes)
        set_genes=set(g)
        print("num genes:",len(g),"num unique:",len(set_genes))
        
    def histogram(self):
        '''
        this was done somewhere else already
        '''
        
        
        
gsea=GSEA()
gsea.load_data("GSE25628_filtered_expression.txt","GSE25628_samples.txt","c2.cp.kegg.v6.2.symbols.filtered.gmt")
#this mirrors self.largest set in class
l = gsea.get_gene_rank_order()
print("*********")
gsea.get_enrichment_score("KEGG_CITRATE_CYCLE_TCA_CYCLE")
print("*********")

gsea.q10()
print("*********")
gsea.q12()


expression genes:    SYMBOL
0     A2M
1  A4GALT
2    AAAS
3    AACS
4   AAGAB
len expression genes: 10702 (10702,)
len expr_gene should be 10k: 10702
------df head--------
   SYMBOL  GSM629719  GSM629721  GSM629723  GSM629726  GSM629728  GSM629730  \
0     A2M  10.782603  12.224706  11.727896  11.807600  12.064787  12.170485   
1  A4GALT   7.468264   7.076519   7.529791   7.172451   7.073430   6.980553   
2    AAAS   7.608572   7.784315   7.958451   8.025649   8.018630   7.375393   
3    AACS   8.400528   8.413255   8.387644   8.548757   8.047159   7.682527   
4   AAGAB   6.292121   5.599561   6.003853   5.749613   5.339957   6.086971   

   GSM629732  GSM629722  GSM629724  GSM629725  GSM629727  GSM629729  GSM629735  
0  12.268920  10.222550  10.196768  11.939311  10.366529  10.594714  10.416336  
1   6.625028   6.435303   6.828313   7.086718   6.331259   6.960688   6.403040  
2   7.705605   7.230928   7.441335   7.459882   7.239895   7.244419   7.352893  
3   7.448159   8.127974   8.1

862 processing gene: SPOCK2
miss subtracting
863 processing gene: HLA-DMA
miss subtracting
864 processing gene: NPTXR
miss subtracting
865 processing gene: GPS2
miss subtracting
866 processing gene: SARS
miss subtracting
867 processing gene: C1orf115
miss subtracting
868 processing gene: TSPYL5
miss subtracting
869 processing gene: XPNPEP2
miss subtracting
870 processing gene: IMP3
miss subtracting
871 processing gene: ZC4H2
miss subtracting
872 processing gene: RP4-781L3.1
miss subtracting
873 processing gene: IFFO1
miss subtracting
874 processing gene: TMEM39B
miss subtracting
875 processing gene: PDGFRB
miss subtracting
876 processing gene: LAMP5
miss subtracting
877 processing gene: CD320
miss subtracting
878 processing gene: PPP1R3C
miss subtracting
879 processing gene: MAP3K6
miss subtracting
880 processing gene: PIGT
miss subtracting
881 processing gene: ICAM1
miss subtracting
882 processing gene: CDIP1
miss subtracting
883 processing gene: KLHDC8A
miss subtracting
884 processin

1612 processing gene: TRO
miss subtracting
1613 processing gene: PVRL2
miss subtracting
1614 processing gene: CITED2
miss subtracting
1615 processing gene: GRHPR
miss subtracting
1616 processing gene: ARHGEF2
miss subtracting
1617 processing gene: RGS9
miss subtracting
1618 processing gene: PKIA
miss subtracting
1619 processing gene: CXCL2
miss subtracting
1620 processing gene: PCIF1
miss subtracting
1621 processing gene: AAR2
miss subtracting
1622 processing gene: RNF41
miss subtracting
1623 processing gene: KDELR1
miss subtracting
1624 processing gene: PPP1R14B
miss subtracting
1625 processing gene: MXRA7
miss subtracting
1626 processing gene: CD300A
miss subtracting
1627 processing gene: SPR
miss subtracting
1628 processing gene: CRELD2
miss subtracting
1629 processing gene: PTPRB
miss subtracting
1630 processing gene: BCR
miss subtracting
1631 processing gene: SOCS1
miss subtracting
1632 processing gene: ARAP1
miss subtracting
1633 processing gene: RBFA
miss subtracting
1634 proces

2487 processing gene: GLG1
miss subtracting
2488 processing gene: COL6A1
miss subtracting
2489 processing gene: TOMM34
miss subtracting
2490 processing gene: VCP
miss subtracting
2491 processing gene: EMID1
miss subtracting
2492 processing gene: ELK1
miss subtracting
2493 processing gene: SNHG17
miss subtracting
2494 processing gene: ARPIN
miss subtracting
2495 processing gene: KIFC3
miss subtracting
2496 processing gene: F5
miss subtracting
2497 processing gene: CHRD
miss subtracting
2498 processing gene: ECHS1
miss subtracting
2499 processing gene: CAMK2N1
miss subtracting
2500 processing gene: HIRIP3
miss subtracting
2501 processing gene: TNFRSF4
miss subtracting
2502 processing gene: PRCC
miss subtracting
2503 processing gene: SLC4A1
miss subtracting
2504 processing gene: SCAP
miss subtracting
2505 processing gene: ETFB
miss subtracting
2506 processing gene: UBE2I
miss subtracting
2507 processing gene: FBXW4
miss subtracting
2508 processing gene: BCAP31
miss subtracting
2509 proces

3362 processing gene: IGHD
miss subtracting
3363 processing gene: DGKD
miss subtracting
3364 processing gene: PPM1G
miss subtracting
3365 processing gene: LILRA6
miss subtracting
3366 processing gene: GID8
miss subtracting
3367 processing gene: HGC6.3
miss subtracting
3368 processing gene: HDLBP
miss subtracting
3369 processing gene: ROR1
miss subtracting
3370 processing gene: PMPCA
miss subtracting
3371 processing gene: TSC22D4
miss subtracting
3372 processing gene: PI4KA
miss subtracting
3373 processing gene: P2RY2
miss subtracting
3374 processing gene: UFD1L
miss subtracting
3375 processing gene: PTPRE
miss subtracting
3376 processing gene: PCSK5
miss subtracting
3377 processing gene: MAPRE3
miss subtracting
3378 processing gene: SSUH2
miss subtracting
3379 processing gene: MAZ
miss subtracting
3380 processing gene: PMVK
miss subtracting
3381 processing gene: MICAL1
miss subtracting
3382 processing gene: OSGEP
miss subtracting
3383 processing gene: CTDNEP1
miss subtracting
3384 proc

...

4805 processing gene: NOD1
miss subtracting
4806 processing gene: BC069004
miss subtracting
4807 processing gene: DENND1A
miss subtracting
4808 processing gene: TFG
miss subtracting
4809 processing gene: CLASRP
miss subtracting
4810 processing gene: APEH
miss subtracting
4811 processing gene: GLP1R
miss subtracting
4812 processing gene: ZFHX2
miss subtracting
4813 processing gene: TBC1D16
miss subtracting
4814 processing gene: TUBB2A
miss subtracting
4815 processing gene: DCLRE1B
miss subtracting
4816 processing gene: METTL17
miss subtracting
4817 processing gene: RPL13
miss subtracting
4818 processing gene: APOL6
miss subtracting
4819 processing gene: ST3GAL5
miss subtracting
4820 processing gene: TMEM38B
miss subtracting
4821 processing gene: CNTD2
miss subtracting
4822 processing gene: SLC26A1
miss subtracting
4823 processing gene: ADAM23
miss subtracting
4824 processing gene: PFDN1
miss subtracting
4825 processing gene: KPTN
miss subtracting
4826 processing gene: TGM1
miss subtract

5680 processing gene: PNMT
miss subtracting
5681 processing gene: OAS3
miss subtracting
5682 processing gene: TSPYL4
miss subtracting
5683 processing gene: LPP
miss subtracting
5684 processing gene: GNL3L
miss subtracting
5685 processing gene: AMIGO3
miss subtracting
5686 processing gene: ZSCAN26
miss subtracting
5687 processing gene: NADSYN1
miss subtracting
5688 processing gene: PRKACG
miss subtracting
5689 processing gene: FZD8
miss subtracting
5690 processing gene: RPL27
miss subtracting
5691 processing gene: ATP5L
miss subtracting
5692 processing gene: TMED9
miss subtracting
5693 processing gene: CARTPT
miss subtracting
5694 processing gene: SLC9A8
miss subtracting
5695 processing gene: KPNA6
miss subtracting
5696 processing gene: SAP30
miss subtracting
5697 processing gene: VEGFA
miss subtracting
5698 processing gene: FNBP1
miss subtracting
5699 processing gene: NR2F6
miss subtracting
5700 processing gene: SLC25A17
miss subtracting
5701 processing gene: PAX5
miss subtracting
5702

6555 processing gene: PHF21A
miss subtracting
6556 processing gene: CHFR
miss subtracting
6557 processing gene: TFDP1
miss subtracting
6558 processing gene: ADI1
miss subtracting
6559 processing gene: CHGA
miss subtracting
6560 processing gene: TOR3A
miss subtracting
6561 processing gene: ATP5J
miss subtracting
6562 processing gene: SRGAP2
miss subtracting
6563 processing gene: ATP6V0E2
miss subtracting
6564 processing gene: LAMTOR5
miss subtracting
6565 processing gene: MNDA
miss subtracting
6566 processing gene: MXD3
miss subtracting
6567 processing gene: CROCCP3
miss subtracting
6568 processing gene: PRDX1
miss subtracting
6569 processing gene: NTRK3
miss subtracting
6570 processing gene: GPR157
miss subtracting
6571 processing gene: C9orf40
miss subtracting
6572 processing gene: GARS
miss subtracting
6573 processing gene: MIR7703
miss subtracting
6574 processing gene: RP13-258O15.1
miss subtracting
6575 processing gene: ENPP1
miss subtracting
6576 processing gene: TSPAN3
miss subtr

7430 processing gene: PDCL
miss subtracting
7431 processing gene: SLFN12
miss subtracting
7432 processing gene: MTF1
miss subtracting
7433 processing gene: SNHG3
miss subtracting
7434 processing gene: CTNNB1
miss subtracting
7435 processing gene: PPP1R3D
miss subtracting
7436 processing gene: FUT2
miss subtracting
7437 processing gene: TMPRSS11D
miss subtracting
7438 processing gene: PMS2L2
miss subtracting
7439 processing gene: STX7
miss subtracting
7440 processing gene: PIGP
miss subtracting
7441 processing gene: NUBPL
miss subtracting
7442 processing gene: MTAP
miss subtracting
7443 processing gene: SETD8
miss subtracting
7444 processing gene: VDAC3
miss subtracting
7445 processing gene: MTL5
miss subtracting
7446 processing gene: DHTKD1
miss subtracting
7447 processing gene: AMPD3
miss subtracting
7448 processing gene: MRPL15
miss subtracting
7449 processing gene: SNORA29
miss subtracting
7450 processing gene: CNBP
miss subtracting
7451 processing gene: FBXW11
miss subtracting
7452

8305 processing gene: SND1-IT1
miss subtracting
8306 processing gene: AKAP13
miss subtracting
8307 processing gene: CHKA
miss subtracting
8308 processing gene: PUM1
miss subtracting
8309 processing gene: PTRH2
miss subtracting
8310 processing gene: BECN1
miss subtracting
8311 processing gene: LOC100129518
miss subtracting
8312 processing gene: AHCYL1
miss subtracting
8313 processing gene: GJA9
miss subtracting
8314 processing gene: CDH16
miss subtracting
8315 processing gene: IL17RB
miss subtracting
8316 processing gene: SSR3
miss subtracting
8317 processing gene: HELZ
miss subtracting
8318 processing gene: NFYB
miss subtracting
8319 processing gene: TBC1D19
miss subtracting
8320 processing gene: ATP11A
miss subtracting
8321 processing gene: SCML2
miss subtracting
8322 processing gene: ARMCX3
miss subtracting
8323 processing gene: FBN2
miss subtracting
8324 processing gene: KHDRBS3
miss subtracting
8325 processing gene: ITGAE
miss subtracting
8326 processing gene: CCDC53
miss subtracti

In [ ]:
f